<a href="https://cognitiveclass.ai"><img src = "https://ibm.box.com/shared/static/9gegpsmnsoo25ikkbl4qzlvlyjbgxs5x.png" width = 400> </a>

<h1 align=center><font size = 5>Where would you open a new Pizza Restaurant in Buenos Aires?</font></h1>

## Introduction

This lab is a task for the Coursera Data Science specialization.

Author: Santiago Maraggi


## Business Problem / Introduction

The goal of this work is to recommend a neighborhood to open a new Pizza Restaurant in Buenos Aires city.

Buenos Aires is a high profile touristic city and the Capital City of Argentina. Founded two times, in 1536 and in 1580, it has a rich colonial history, being the focus of two big scale invasions during the beginning 19th Century and a very important hub for commerce and politics since the 18th. Currently, the city’s Italian influences in food and general culture are widely known and it is also famous for being the origin of Tango music.

Pizza, on the other hand, is the most well known Italian dish all over the world. Businessmen and investors always struggle to decide good places to set new businesses.

Finding an appropriate environment for an entrepreneurship is a challenging task, to ensure best chances for the business to flourish. Best places for common business, however, tend to be overpopulated with well-established actors.

This work proposes to apply some basic data science techniques combined with geographical information in order to group common neighborhoods and select from the best possible group, the neighborhood less populated with Pizza Restaurants.

## Data Section

At first, the neighborhood information will be extracted from the official Buenos Aires Government Data service (BA Data).

Official website is: https://data.buenosaires.gob.ar/

From this data service, the neighborhood areas will be obtained, and from this areas the geographical centroid will be determined. A radius distance will be calculated from each neighborhood area, so that that area will be considered as if it were obtained from a perfect circle, and from that radius a fraction of 3/4 will be considered.

Buenos Aires neighborhoods geojson data: http://cdn.buenosaires.gob.ar/datosabiertos/datasets/barrios/barrios.geojson

Once the neighborhoods centers and radio distances are determined, the FourSquare API will be used to get the venues representative for each neighborhood.

The most common venue types for each neighborhood will be determined, and from this common data, neighborhood clusters will be determined with a K-Means cluster algorithm. As it was detailed, the "best cluster" will be the one with more Pizza Restaurants, while the "best neighborhood" will be the one with less pizza restaurants from the "best cluster".

## Methodology

In order to fulfill the purpose of this work, neighborhoods are going to be clustered in groups by similarities in the most common venues in each one of them.

The cluster with proportionally more Pizza Restaurants on it will be considered the most interesting to open a new business of this type, and then, the neighborhood from this cluster with less Pizza Restaurants will be considered a good candidate to open the new pizza shop.

This model makes a few assumptions and simplifications:

- The business is assumed to be of a well established brand, so the aim is to compete in interesting places, rather than set a restaurant in areas completely without pizza restaurants.
- The neighborhood clusters are assumed to be representative at some point.
- Neighborhood clusters with most pizza restaurants are considered to have common properties that makes them interesting for this kind of business.
- From the "most interesting cluster of neighborhoods", extracted with the mentioned criteria, and given that clusters are considered to be representative of common features that make them interesting for the target business type, the neighborhood with less pizza restaurants will be considered "underexploited", but still interesting.
- Venues for each neighborhood will be obtained by the FourSquare public API.
- Venues will be obtained from the geographic centroid of each neighborhood, within a radius proportionally related to the overall neighborhood area. This could leave some venues near the border of each neighborhood outside consideration, so we are assuming that statistically this will not be very significant.
- Centroid of neighborhoods, as they are not provided by BA Data service, will be calculated from the neighborhood polygon averaging extreme latitude and longitude, a fast method that is still  considered to be representative.
- Of course, the first assumption is still that you want to open a Pizza Restaurant in Buenos Aires.

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1. <a href="#item1">Download and Explore Dataset</a>

2. <a href="#item2">Explore Neighborhoods in Buenos Aires</a>

3. <a href="#item3">Analyze Each Neighborhood</a>

4. <a href="#item4">Cluster Neighborhoods</a>

5. <a href="#item5">Examine Clusters</a>    
</font>
</div>

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.5.11
  latest version: 4.8.2

Please update conda by running

    $ conda update -n base -c defaults conda



# All requested packages already installed.

Libraries imported.


### 0. Download and explore Buenos Aires Datasets

## Links
BA Data homepage: 
https://data.buenosaires.gob.ar/

Neighborhoods GeoJSON:
http://cdn.buenosaires.gob.ar/datosabiertos/datasets/barrios/barrios.geojson

In [2]:
import urllib.request, json

# load neigbourhoods geojson in variable 'ba_data'
with urllib.request.urlopen("http://cdn.buenosaires.gob.ar/datosabiertos/datasets/barrios/barrios.geojson") as url:
    ba_data = json.loads(url.read().decode())

# save geojson locally for backup purposes
with open('ba_data.geojson', 'w') as baneighborhoodsgeojsonfile:
      json.dump(ba_data, baneighborhoodsgeojsonfile)

neighborhoods_data = ba_data['features']
for feature in neighborhoods_data:
    print (feature['properties']['barrio'])

CHACARITA
PATERNAL
VILLA CRESPO
VILLA DEL PARQUE
ALMAGRO
CABALLITO
VILLA SANTA RITA
MONTE CASTRO
VILLA REAL
FLORES
FLORESTA
CONSTITUCION
SAN CRISTOBAL
BOEDO
VELEZ SARSFIELD
VILLA LURO
PARQUE PATRICIOS
MATADEROS
VILLA LUGANO
SAN TELMO
SAAVEDRA
COGHLAN
VILLA URQUIZA
COLEGIALES
BALVANERA
VILLA GRAL. MITRE
PARQUE CHAS
AGRONOMIA
VILLA ORTUZAR
BARRACAS
PARQUE AVELLANEDA
PARQUE CHACABUCO
NUEVA POMPEYA
PALERMO
VILLA RIACHUELO
VILLA SOLDATI
VILLA PUEYRREDON
VILLA DEVOTO
LINIERS
VERSALLES
PUERTO MADERO
MONSERRAT
SAN NICOLAS
BELGRANO
RECOLETA
RETIRO
NUÑEZ
BOCA


<a id='item1'></a>

## 1. Download and Explore Dataset

#### Load and explore the data

Next, let's load the data.

Let's take a quick look at the data.

In [3]:
# dataframe column names
column_names = ['neighborhood', 'commune', 'area', 'latitude', 'longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

# still, print data of 1st neighborhood from the original data to verify data format
neighborhoods_data[0]

{'type': 'Feature',
 'properties': {'barrio': 'CHACARITA',
  'comuna': 15,
  'perimetro': 7724.85295457,
  'area': 3115707.10627},
 'geometry': {'type': 'Polygon',
  'coordinates': [[[-58.4528200492791, -34.5959886570639],
    [-58.453655193137, -34.5965557163041],
    [-58.4537674321647, -34.5966342484152],
    [-58.4538163134148, -34.5966684788922],
    [-58.4547947928051, -34.5973527273644],
    [-58.4554840815948, -34.5978347610252],
    [-58.4559204833296, -34.5976953435829],
    [-58.4560093721285, -34.5976669530232],
    [-58.4560576047802, -34.5976515472868],
    [-58.4562363723257, -34.5975900748435],
    [-58.4564940053845, -34.597501563774],
    [-58.4570733158433, -34.5973024999733],
    [-58.4576142986162, -34.5971165306991],
    [-58.4578298572666, -34.5970394940224],
    [-58.4579314199407, -34.5970031094655],
    [-58.4579383597537, -34.5970006235554],
    [-58.457939151188, -34.5970004324802],
    [-58.4580314840712, -34.5969781271249],
    [-58.4582467474022, -34.5969

Notice how all the relevant data is in the *features* key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.

#### Tranform the data into a *pandas* dataframe

The next task is essentially transforming this data of nested Python dictionaries into a *pandas* dataframe. So let's start by creating an empty dataframe.

Take a look at the empty dataframe to confirm that the columns are as intended.

In [4]:
neighborhoods

Empty DataFrame
Columns: [neighborhood, commune, area, latitude, longitude]
Index: []

In [5]:
import math

def calculateNeighborhoodRadius(neighborhood_area):
    return (math.sqrt(neighborhood_area / math.pi) * 3 / 4)

Then let's loop through the data and fill the dataframe one row at a time.

In [6]:
for data in neighborhoods_data:
    neighborhood = data['properties']['barrio']
    commune = data['properties']['comuna']
    area = data['properties']['area']
    
    geo_area = pd.DataFrame(data['geometry']['coordinates'][0])
    
    # Averaging all points of geometry is not representative: 
    # Irregular small edges have unfair more weight than long important linear borders
    # centroid = geo_area.mean()
    # longitude = centroid[0]
    # latitude = centroid[1]
    
    # A better approach is to use extreme values:
    # Small detailed irregular edges are not more considered than long segments
    long_max = np.amax(geo_area[0])
    long_min = np.amin(geo_area[0])
    longitude = (long_max + long_min) / 2

    lat_max = np.amax(geo_area[1])
    lat_min = np.amin(geo_area[1])
    latitude = (lat_max + lat_min) / 2
    radius = calculateNeighborhoodRadius(area)
    # unpaid geographical services fail very often agains repeated queries, 
    # although repetitive retry is an option, 
    # still, the results with this approach proved to be a good approximation
    
    if (neighborhood == 'PALERMO'):
        print("Printing as example Palermo neighborhood centroid data...")
        print("Long max: ", long_max, " Long min: ", long_min)
        print("Latitude of Palermo's Center: ", latitude)
        print("Longitude of Palermo's Center: ", longitude)
        
    data['latitude'] = latitude
    data['longitude'] = longitude
    data['radius'] = radius
            
    neighborhoods = neighborhoods.append({'neighborhood': neighborhood,
                            'commune': commune,
                            'area': area,
                            'latitude': latitude,
                            'longitude': longitude,
                            'radius': radius}, ignore_index=True)

Printing as example Palermo neighborhood centroid data...
Long max:  -58.3928393282688  Long min:  -58.4490443843996
Latitude of Palermo's Center:  -34.5743954065225
Longitude of Palermo's Center:  -58.420941856334196


Quickly examine the resulting dataframe.

In [7]:
neighborhoods.head()

neighborhood commune          area   latitude  longitude      radius
0         CHACARITA      15  3.115707e+06 -34.588065 -58.452682  746.903749
1          PATERNAL      15  2.229829e+06 -34.596378 -58.467534  631.861814
2      VILLA CRESPO      15  3.615978e+06 -34.598142 -58.441151  804.635501
3  VILLA DEL PARQUE      11  3.399596e+06 -34.605902 -58.490092  780.189244
4           ALMAGRO       5  4.050752e+06 -34.609894 -58.422626  851.636306

In [8]:
neighborhoods = neighborhoods.drop_duplicates()
neighborhoods["neighborhood"]

0             CHACARITA
1              PATERNAL
2          VILLA CRESPO
3      VILLA DEL PARQUE
4               ALMAGRO
5             CABALLITO
6      VILLA SANTA RITA
7          MONTE CASTRO
8            VILLA REAL
9                FLORES
10             FLORESTA
11         CONSTITUCION
12        SAN CRISTOBAL
13                BOEDO
14      VELEZ SARSFIELD
15           VILLA LURO
16     PARQUE PATRICIOS
17            MATADEROS
18         VILLA LUGANO
19            SAN TELMO
20             SAAVEDRA
21              COGHLAN
22        VILLA URQUIZA
23           COLEGIALES
24            BALVANERA
25    VILLA GRAL. MITRE
26          PARQUE CHAS
27            AGRONOMIA
28        VILLA ORTUZAR
29             BARRACAS
30    PARQUE AVELLANEDA
31     PARQUE CHACABUCO
32        NUEVA POMPEYA
33              PALERMO
34      VILLA RIACHUELO
35        VILLA SOLDATI
36     VILLA PUEYRREDON
37         VILLA DEVOTO
38              LINIERS
39            VERSALLES
40        PUERTO MADERO
41            MO

#### Use geopy library to get the latitude and longitude values of Buenos Aires City.

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>buenosaires_explorer</em>, as shown below.

In [9]:
address = 'Buenos Aires, Argentina'
geolocator = Nominatim(user_agent="buenosaires_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print ('The geographical coordinate of Buenos Aires City are {}, {}.'.format(latitude, longitude))

The geographical coordinate of Buenos Aires City are -34.6075682, -58.4370894.


#### Create a map of Buenos Aires with neighborhoods superimposed on top.

In [10]:
map_ba_full = folium.Map(location=[latitude, longitude], zoom_start=11)

for neighborhood in neighborhoods_data:
        # print(lat, lon, area_name)
        label = neighborhood['properties']['barrio']
        area = neighborhood['properties']['area']
        geometry = neighborhood['geometry']
        label = folium.Popup(label, parse_html=True)
        
        folium.GeoJson(geometry).add_to(map_ba_full)

map_ba_full

In [11]:
map_ba = folium.Map(location=[latitude, longitude], zoom_start=10)

for lat, lon, area_name in zip(neighborhoods['latitude'], neighborhoods['longitude'], neighborhoods['neighborhood']):
        # print(lat, lon, area_name)
        label = area_name
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lon],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(map_ba)
map_ba

In [12]:
map_ba_full2 = folium.Map(location=[latitude, longitude], zoom_start=11)

for neighborhood in neighborhoods_data:
        # print(lat, lon, area_name)
        label = neighborhood['properties']['barrio']
        area = neighborhood['properties']['area']
        geometry = neighborhood['geometry']
        latitude = neighborhood['latitude']
        longitude = neighborhood['longitude']
        label = folium.Popup(label, parse_html=True)
        
        folium.GeoJson(geometry).add_to(map_ba_full2)
        
        folium.CircleMarker(
            [latitude, longitude],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(map_ba_full2)

map_ba_full2

In [13]:
map_ba_full3 = folium.Map(location=[latitude, longitude], zoom_start=11)

for neighborhood in neighborhoods_data:
        # print(lat, lon, area_name)
        label = neighborhood['properties']['barrio']
        area = neighborhood['properties']['area']
        geometry = neighborhood['geometry']
        latitude = neighborhood['latitude']
        longitude = neighborhood['longitude']
        radius = neighborhood['radius']
        label = folium.Popup(label, parse_html=True)
        
        folium.GeoJson(geometry).add_to(map_ba_full3)
        
        folium.CircleMarker(
            [latitude, longitude],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(map_ba_full3)
        
        folium.Circle(
            [latitude, longitude],
            radius=radius,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.4).add_to(map_ba_full3)

map_ba_full3

**Folium** is a great visualization library. Feel free to zoom into the above map, and click on each circle mark to reveal the name of the neighborhood and its respective borough.

However, for illustration purposes, let's simplify the above map and segment and cluster only the neighborhood of Wychwood. So let's slice the original dataframe and create a new dataframe of the Wychwood data.

In [14]:
palermo_data = neighborhoods[neighborhoods['neighborhood'] == "PALERMO"].reset_index(drop=True)
palermo_data.head()

neighborhood commune          area   latitude  longitude       radius
0      PALERMO      14  1.584587e+07 -34.574395 -58.420942  1684.396728

Let's get the geographical coordinates of Wychwood

In [15]:
address = 'Palermo, Buenos Aires'
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Palermo obtained by geolocator are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Palermo obtained by geolocator are -34.5803362, -58.4245236.


Visualize Palermo in the map

In [16]:
map_palermo = folium.Map(location=[latitude, longitude], zoom_start=11)
# add markers to map
for lat, lon, label in zip(palermo_data['latitude'], palermo_data['longitude'], palermo_data['area']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_palermo)  
    
map_palermo

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [17]:
# @hidden_cell
CLIENT_ID = 'JUZMOXW4YXHMROIURRKI5IPQVJ401DG34B2EIRIIQCSL4B2S' # 'your-client-ID' # your Foursquare ID
CLIENT_SECRET = 'GT5DAZ3LYESG3WCMARD32GUEIF4BF2KFCGENJBRE4FTKCA43' # 'your-client-secret' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
# print('CLIENT_ID: ' + CLIENT_ID)
# print('CLIENT_SECRET:' + CLIENT_SECRET)
print('CLIENT_ID: ' + 'client ID stored in variable CLIENT_ID')
print('CLIENT_SECRET:' + 'client SECRET stored in variable CLIENT_SECRET')

Your credentails:
CLIENT_ID: client ID stored in variable CLIENT_ID
CLIENT_SECRET:client SECRET stored in variable CLIENT_SECRET


#### Let's explore the first neighborhood in our dataframe.

Get the neighborhood's name.

In [18]:
palermo_data.loc[0, 'neighborhood']

'PALERMO'

Get the neighborhood's latitude and longitude values. Also define radius to consider neighborhood venues.

In [19]:
neighborhood_latitude = palermo_data.loc[0, 'latitude'] # neighborhood latitude value
neighborhood_longitude = palermo_data.loc[0, 'longitude'] # neighborhood longitude value

neighborhood_name = palermo_data.loc[0, 'neighborhood'] # neighborhood name

neighborhood_area = palermo_data.loc[0, 'area'] # neighborhood area in squared meters

neighborhood_radius = calculateNeighborhoodRadius(neighborhood_area)

print('Latitude and longitude values of {} are {}, {}. Radius is {}'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude,
                                                               neighborhood_radius))

Latitude and longitude values of PALERMO are -34.5743954065225, -58.420941856334196. Radius is 1684.3967276056228


#### Now, let's get the top 100 venues that are in Palermo center within the calculated radius in meters.

First, let's create the GET request URL. Name your URL **url**.

In [20]:
# @hidden_cell

LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = neighborhood_radius # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
# url # display URL this shows the client ID and SECRET
print ('Test URL properly set')



Test URL properly set


Send the GET request and examine the resutls

In [21]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e517a6d0be7b4001bddff70'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Palermo',
  'headerFullLocation': 'Palermo, Buenos Aires',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 198,
  'suggestedBounds': {'ne': {'lat': -34.55923939136648,
    'lng': -58.40256937636699},
   'sw': {'lat': -34.589551421678514, 'lng': -58.4393143363014}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '54307e25498ea11026f13c22',
       'name': 'Boûlan',
       'location': {'address': 'Sinclair 3196',
        'crossStreet': 'esq. Juan Francisco Seguí',
        'lat': -34.57305128745807,
        'lng': -58.42241057698123,
        'labeledLatLngs'

From the Foursquare lab in the previous module, we know that all the information is in the *items* key. Before we proceed, let's borrow the **get_category_type** function from the Foursquare lab.

In [22]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [23]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name categories        lat  \
0                                        Boûlan     Bakery -34.573051   
1                        Open Park Club Rosedal        Gym -34.573133   
2  Circuito El Rosedal - Pista de entrenamiento      Track -34.570896   
3                                Tea Connection   Tea Room -34.574779   
4                                  Dazzler Polo      Hotel -34.576041   

         lng  
0 -58.422411  
1 -58.421057  
2 -58.420851  
3 -58.423367  
4 -58.424110

And how many venues were returned by Foursquare?

In [24]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


<a id='item2'></a>

## 2. Explore Neighborhoods in Buenos Aires

#### Let's create a function to repeat the same process to all the neighborhoods in Buenos Aires, for testing, first around Palermo

In [25]:
def getNearbyVenues(names, latitudes, longitudes, radius):
    
    venues_list=[]
    for name, lat, lng, rad in zip(names, latitudes, longitudes, radius):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            rad, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now run the above function on each neighborhood and create a new dataframe called *palermo_venues*.

In [26]:
palermo_venues = getNearbyVenues(palermo_data['neighborhood'],
                                   latitudes=palermo_data['latitude'],
                                   longitudes=palermo_data['longitude'],
                                   radius=palermo_data['radius']
                                  )
print(palermo_venues)

PALERMO
   Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0       PALERMO             -34.574395              -58.420942   
1       PALERMO             -34.574395              -58.420942   
2       PALERMO             -34.574395              -58.420942   
3       PALERMO             -34.574395              -58.420942   
4       PALERMO             -34.574395              -58.420942   
5       PALERMO             -34.574395              -58.420942   
6       PALERMO             -34.574395              -58.420942   
7       PALERMO             -34.574395              -58.420942   
8       PALERMO             -34.574395              -58.420942   
9       PALERMO             -34.574395              -58.420942   
10      PALERMO             -34.574395              -58.420942   
11      PALERMO             -34.574395              -58.420942   
12      PALERMO             -34.574395              -58.420942   
13      PALERMO             -34.574395              -58.420942   
14

#### Let's check the size of the resulting dataframe

In [27]:
print(palermo_venues.shape)
palermo_venues.head()

(100, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      PALERMO             -34.574395              -58.420942   
1      PALERMO             -34.574395              -58.420942   
2      PALERMO             -34.574395              -58.420942   
3      PALERMO             -34.574395              -58.420942   
4      PALERMO             -34.574395              -58.420942   

                                          Venue  Venue Latitude  \
0                                        Boûlan      -34.573051   
1                        Open Park Club Rosedal      -34.573133   
2  Circuito El Rosedal - Pista de entrenamiento      -34.570896   
3                                Tea Connection      -34.574779   
4                                  Dazzler Polo      -34.576041   

   Venue Longitude Venue Category  
0       -58.422411         Bakery  
1       -58.421057            Gym  
2       -58.420851          Track  
3       -58.423367       Tea Room  
4       -58.424110          Hotel

Let's check how many venues were returned for each neighborhood

In [28]:
palermo_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                         
PALERMO                         100                     100    100   

              Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                   
PALERMO                  100              100             100

#### Let's find out how many unique categories can be curated from all the returned venues

In [29]:
print('There are {} uniques categories.'.format(len(palermo_venues['Venue Category'].unique())))

There are 61 uniques categories.


<a id='item3'></a>

## 3. Analyze Each Neighborhood

In [30]:
# one hot encoding
palermo_onehot = pd.get_dummies(palermo_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
palermo_onehot['Neighborhood'] = palermo_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [palermo_onehot.columns[-1]] + list(palermo_onehot.columns[:-1])
palermo_onehot = palermo_onehot[fixed_columns]

palermo_onehot.head()

Neighborhood  American Restaurant  Argentinian Restaurant  Art Museum  \
0      PALERMO                    0                       0           0   
1      PALERMO                    0                       0           0   
2      PALERMO                    0                       0           0   
3      PALERMO                    0                       0           0   
4      PALERMO                    0                       0           0   

   Asian Restaurant  Athletics & Sports  BBQ Joint  Bakery  Bar  Beer Bar  \
0                 0                   0          0       1    0         0   
1                 0                   0          0       0    0         0   
2                 0                   0          0       0    0         0   
3                 0                   0          0       0    0         0   
4                 0                   0          0       0    0         0   

   Bistro  Bookstore  Botanical Garden  Boutique  Breakfast Spot  Brewery  \
0       0          0                 0         0               0        0   
1       0          0                 0         0               0        0   
2       0          0                 0         0               0        0   
3       0          0                 0         0               0        0   
4       0          0                 0         0               0        0   

   Café  Chocolate Shop  Cocktail Bar  Coffee Shop  Convention Center  \
0     0               0             0            0                  0   
1     0               0             0            0                  0   
2     0               0             0            0                  0   
3     0               0             0            0                  0   
4     0               0             0            0                  0   

   Creperie  Cuban Restaurant  Event Space  French Restaurant  Garden  Gym  \
0         0                 0            0                  0       0    0   
1         0                 0            0                  0       0    1   
2         0                 0            0                  0       0    0   
3         0                 0            0                  0       0    0   
4         0                 0            0                  0       0    0   

   Gym / Fitness Center  History Museum  Hotel  Ice Cream Shop  \
0                     0               0      0               0   
1                     0               0      0               0   
2                     0               0      0               0   
3                     0               0      0               0   
4                     0               0      1               0   

   Italian Restaurant  Japanese Restaurant  Jewish Restaurant  Juice Bar  \
0                   0                    0                  0          0   
1                   0                    0                  0          0   
2                   0                    0                  0          0   
3                   0                    0                  0          0   
4                   0                    0                  0          0   

   Middle Eastern Restaurant  Nightclub  Noodle House  Other Great Outdoors  \
0                          0          0             0                     0   
1                          0          0             0                     0   
2                          0          0             0                     0   
3                          0          0             0                     0   
4                          0          0             0                     0   

   Paper / Office Supplies Store  Park  Peruvian Restaurant  Pizza Place  \
0                              0     0                    0            0   
1                              0     0                    0            0   
2                              0     0                    0            0   
3                              0     0                    0            0   
4       

And let's examine the new dataframe size.

In [31]:
palermo_onehot.shape

(100, 62)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [32]:
palermo_grouped = palermo_onehot.groupby('Neighborhood').mean().reset_index()
palermo_grouped

Neighborhood  American Restaurant  Argentinian Restaurant  Art Museum  \
0      PALERMO                 0.01                    0.09        0.02   

   Asian Restaurant  Athletics & Sports  BBQ Joint  Bakery   Bar  Beer Bar  \
0              0.01                0.01       0.02    0.03  0.01      0.02   

   Bistro  Bookstore  Botanical Garden  Boutique  Breakfast Spot  Brewery  \
0    0.01       0.01              0.01      0.01            0.01     0.02   

   Café  Chocolate Shop  Cocktail Bar  Coffee Shop  Convention Center  \
0  0.02            0.01          0.01         0.01               0.01   

   Creperie  Cuban Restaurant  Event Space  French Restaurant  Garden   Gym  \
0      0.01              0.01         0.01               0.01    0.02  0.02   

   Gym / Fitness Center  History Museum  Hotel  Ice Cream Shop  \
0                  0.03            0.01   0.04            0.04   

   Italian Restaurant  Japanese Restaurant  Jewish Restaurant  Juice Bar  \
0                0.05                 0.03               0.01       0.01   

   Middle Eastern Restaurant  Nightclub  Noodle House  Other Great Outdoors  \
0                       0.02       0.01          0.01                  0.01   

   Paper / Office Supplies Store  Park  Peruvian Restaurant  Pizza Place  \
0                           0.01  0.01                 0.01         0.01   

   Planetarium  Plaza   Pub  Racecourse  Restaurant  Science Museum  \
0         0.01   0.04  0.02        0.01        0.02            0.01   

   Shopping Mall  Speakeasy  Sports Bar  Sports Club  Stadium  \
0           0.01       0.01        0.01         0.01     0.01   

   Sushi Restaurant  Tea Room  Tennis Court  Theme Park  Track  Wine Bar  \
0              0.02      0.01          0.01        0.01   0.01      0.01   

   Wine Shop  Women's Store  
0       0.02           0.01

#### Let's confirm the new size

In [33]:
palermo_grouped.shape

(1, 62)

In [34]:
neighborhoods.shape

(48, 6)

In [35]:
# Neighborhoods belong to Communes in Buenos Aires
# Neighborhoods do not have official sub-areas to consider sepparately

# Call the API of Foursquare and then save locally the results
# This is done in order to avoid saturating the API with calls through tests, 
# given that we are using the free version with restricted calls

import os.path

# if json is not locally saved, ask for it to the online service

if not os.path.isfile("buenosaires_venues.csv"):
    buenosaires_venues = getNearbyVenues(neighborhoods['neighborhood'],
                                   latitudes=neighborhoods['latitude'],
                                   longitudes=neighborhoods['longitude'],
                                   radius=neighborhoods['radius']
                                  )

    buenosaires_venues.to_csv("buenosaires_venues.csv")
    print("saved local query back up in buenosaires_venues.csv file")
else:
    print("loaded local query back up from buenosaires_venues.csv file")
    buenosaires_venues = pd.read_csv("buenosaires_venues.csv") 
    
print(buenosaires_venues.shape)
buenosaires_venues.head()

loaded local query back up from buenosaires_venues.csv file
(2042, 8)


Unnamed: 0 Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           0    CHACARITA             -34.588065              -58.452682   
1           1    CHACARITA             -34.588065              -58.452682   
2           2    CHACARITA             -34.588065              -58.452682   
3           3    CHACARITA             -34.588065              -58.452682   
4           4    CHACARITA             -34.588065              -58.452682   

                    Venue  Venue Latitude  Venue Longitude  \
0  Sede Central de Whisky      -34.586750       -58.450596   
1  El Imperio de la Pizza      -34.586890       -58.454967   
2             Santos 4040      -34.588822       -58.449863   
3                  Donnet      -34.588333       -58.450745   
4    Albamonte Ristorante      -34.587803       -58.453075   

                  Venue Category  
0                     Whisky Bar  
1                    Pizza Place  
2                        Theater  
3  Vegetarian / Vegan Restaurant  
4         Argentinian Restaurant

In [36]:
# Let's count how many venues are per neighborhood
buenosaires_venues.groupby('Neighborhood').count()

Unnamed: 0  Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                   
AGRONOMIA                  13                     13                      13   
ALMAGRO                    82                     82                      82   
BALVANERA                  76                     76                      76   
BARRACAS                   20                     20                      20   
BELGRANO                  100                    100                     100   
BOCA                       20                     20                      20   
BOEDO                      31                     31                      31   
CABALLITO                 100                    100                     100   
CHACARITA                  53                     53                      53   
COGHLAN                    12                     12                      12   
COLEGIALES                 54                     54                      54   
CONSTITUCION               23                     23                      23   
FLORES                    100                    100                     100   
FLORESTA                   20                     20                      20   
LINIERS                    19                     19                      19   
MATADEROS                  20                     20                      20   
MONSERRAT                  71                     71                      71   
MONTE CASTRO               14                     14                      14   
NUEVA POMPEYA              12                     12                      12   
NUÑEZ                      87                     87                      87   
PALERMO                   100                    100                     100   
PARQUE AVELLANEDA          12                     12                      12   
PARQUE CHACABUCO           29                     29                      29   
PARQUE CHAS                10                     10                      10   
PARQUE PATRICIOS           28                     28                      28   
PATERNAL                    7                      7                       7   
PUERTO MADERO              67                     67                      67   
RECOLETA                  100                    100                     100   
RETIRO                     42                     42                      42   
SAAVEDRA                   66                     66                      66   
SAN CRISTOBAL              26                     26                      26   
SAN NICOLAS               100                    100                     100   
SAN TELMO                  92                     92                      92   
VELEZ SARSFIELD            14                     14                      14   
VERSALLES                  13                     13                      13   
VILLA CRESPO               76                     76                      76   
VILLA DEL PARQUE           28                     28                      28   
VILLA DEVOTO               78                     78                      78   
VILLA GRAL. MITRE          13                     13                      13   
VILLA LUGANO                9                      9                       9   
VILLA LURO                 21                     21                      21   
VILLA ORTUZAR              25                     25                      25   
VILLA PUEYRREDON           20                     20                      20   
VILLA REAL                 14                     14                      14   
VILLA RIACHUELO             6                      6                       6   
VILLA SANTA RITA           12                     12                      12   
VILLA SOLDATI               7                      7                       7   
VILLA URQUIZA             100                    100                     100   

                  

In [37]:
# Find how many unique categories are within the returned results
print('There are {} uniques categories.'.format(len(buenosaires_venues['Venue Category'].unique())))

There are 233 uniques categories.


In [38]:
# one hot encoding
buenosaires_onehot = pd.get_dummies(buenosaires_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
buenosaires_onehot['Neighborhood'] = buenosaires_venues['Neighborhood'] 

# move neighborhood column to the first column
cols = list(buenosaires_onehot)
cols.insert(0, cols.pop(cols.index('Neighborhood')))
buenosaires_onehot = buenosaires_onehot.loc[:, cols]

buenosaires_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  American Restaurant  \
0    CHACARITA                  0               0                    0   
1    CHACARITA                  0               0                    0   
2    CHACARITA                  0               0                    0   
3    CHACARITA                  0               0                    0   
4    CHACARITA                  0               0                    0   

   Arcade  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                       0            0           0   
1       0                       0            0           0   
2       0                       0            0           0   
3       0                       0            0           0   
4       0                       1            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auto Garage  Auto Workshop  BBQ Joint  Bagel Shop  \
0                   0            0              0          0           0   
1                   0            0              0          0           0   
2                   0            0              0          0           0   
3                   0            0              0          0           0   
4                   0            0              0          0           0   

   Bakery  Bar  Basketball Court  Basketball Stadium  Bed & Breakfast  \
0       0    0                 0                   0                0   
1       0    0                 0                   0                0   
2       0    0                 0                   0                0   
3       0    0                 0                   0                0   
4       0    0                 0                   0                0   

   Beer Bar  Beer Garden  Belgian Restaurant  Big Box Store  \
0         0            0                   0              0   
1         0            0                   0              0   
2         0            0                   0              0   
3         0            0                   0              0   
4         0            0                   0              0   

   Bike Rental / Bike Share  Bike Shop  Bistro  Boat or Ferry  Bookstore  \
0                         0          0       0              0          0   
1                         0          0       0              0          0   
2                         0          0       0              0          0   
3                         0          0       0              0          0   
4                         0          0       0              0          0   

   Botanical Garden  Boutique  Breakfast Spot  Brewery  Buffet  Burger Joint  \
0                 0         0               0        0       0             0   
1                 0         0               0        0       0             0   
2                 0         0               0        0       0             0   
3                 0         0               0        0       0             0   
4                 0         0               0        0       0             0   

   Bus Station  Bus Stop  Butcher  Cafeteria  Café  Camera Store  Candy Store  \
0            0         0        0          0     0             0            0   
1            0         0        0          0     0             0            0   
2            0         0        0          0     0             0            0   
3            0         0        0          0     0             0            0   
4            0         0        0          0     0             0            0   

   Cheese Shop  Chinese Restaurant  Chocolate Shop  Church  Clothing Store  \
0        

In [39]:
buenosaires_onehot.shape

(2042, 234)

In [40]:
buenosaires_grouped = buenosaires_onehot.groupby('Neighborhood').mean().reset_index()
buenosaires_grouped

Neighborhood  Accessories Store  Adult Boutique  American Restaurant  \
0           AGRONOMIA               0.00        0.000000             0.000000   
1             ALMAGRO               0.00        0.000000             0.000000   
2           BALVANERA               0.00        0.013158             0.000000   
3            BARRACAS               0.00        0.000000             0.000000   
4            BELGRANO               0.00        0.000000             0.000000   
5                BOCA               0.00        0.000000             0.000000   
6               BOEDO               0.00        0.000000             0.000000   
7           CABALLITO               0.00        0.000000             0.000000   
8           CHACARITA               0.00        0.000000             0.000000   
9             COGHLAN               0.00        0.000000             0.000000   
10         COLEGIALES               0.00        0.000000             0.000000   
11       CONSTITUCION               0.00        0.000000             0.000000   
12             FLORES               0.01        0.000000             0.000000   
13           FLORESTA               0.00        0.000000             0.000000   
14            LINIERS               0.00        0.000000             0.000000   
15          MATADEROS               0.00        0.000000             0.000000   
16          MONSERRAT               0.00        0.000000             0.000000   
17       MONTE CASTRO               0.00        0.000000             0.000000   
18      NUEVA POMPEYA               0.00        0.000000             0.000000   
19              NUÑEZ               0.00        0.000000             0.011494   
20            PALERMO               0.00        0.000000             0.010000   
21  PARQUE AVELLANEDA               0.00        0.000000             0.000000   
22   PARQUE CHACABUCO               0.00        0.000000             0.000000   
23        PARQUE CHAS               0.00        0.000000             0.000000   
24   PARQUE PATRICIOS               0.00        0.000000             0.000000   
25           PATERNAL               0.00        0.000000             0.000000   
26      PUERTO MADERO               0.00        0.000000             0.000000   
27           RECOLETA               0.00        0.000000             0.010000   
28             RETIRO               0.00        0.000000             0.000000   
29           SAAVEDRA               0.00        0.000000             0.015152   
30      SAN CRISTOBAL               0.00        0.000000             0.000000   
31        SAN NICOLAS               0.00        0.000000             0.000000   
32          SAN TELMO               0.00        0.000000             0.000000   
33    VELEZ SARSFIELD               0.00        0.000000             0.000000   
34          VERSALLES               0.00        0.000000             0.000000   
35       VILLA CRESPO               0.00        0.000000             0.000000   
36   VILLA DEL PARQUE               0.00        0.000000             0.000000   
37       VILLA DEVOTO               0.00        0.000000             0.000000   
38  VILLA GRAL. MITRE               0.00        0.000000             0.000000   
39       VILLA LUGANO               0.00        0.000000             0.000000   
40         VILLA LURO               0.00        0.000000             0.000000   
41      VILLA ORTUZAR               0.00        0.000000             0.000000   
42   VILLA PUEYRREDON               0.00        0.000000             0.000000   
43         VILLA REAL               0.00        0.000000             0.000000   
44    VILLA RIACHUELO               0.00        0.000000             0.000000   
45   VILLA SANTA RITA               0.00        0.000000             0.000000   
46      VILLA SOLDATI               0.00        0.000000             0.000000   
47      VILLA URQUIZA               0.00        0.000000             0.020000   

      Arcade  Argentinian Restaurant  A

In [41]:
buenosaires_grouped.shape

(48, 234)

#### Let's print each neighborhood along with the top 5 most common venues

In [42]:
num_top_venues = 5

for hood in buenosaires_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = buenosaires_grouped[buenosaires_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----AGRONOMIA----
           venue  freq
0   Soccer Field  0.15
1     Restaurant  0.08
2  Train Station  0.08
3  Garden Center  0.08
4    Pizza Place  0.08


----ALMAGRO----
                    venue  freq
0  Argentinian Restaurant  0.12
1          Ice Cream Shop  0.10
2             Pizza Place  0.09
3                    Café  0.06
4                     Bar  0.05


----BALVANERA----
                  venue  freq
0                  Café  0.12
1                 Hotel  0.09
2           Pizza Place  0.05
3   Japanese Restaurant  0.05
4  Fast Food Restaurant  0.04


----BARRACAS----
                    venue  freq
0  Argentinian Restaurant  0.15
1                    Café  0.15
2          Clothing Store  0.10
3           Auto Workshop  0.10
4                   Plaza  0.05


----BELGRANO----
                    venue  freq
0                    Café  0.08
1             Pizza Place  0.06
2               BBQ Joint  0.06
3      Italian Restaurant  0.05
4  Argentinian Restaurant  0.05


----BOCA--

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [43]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 50 venues for each neighborhood.

In [44]:
# num_top_venues = 10
num_top_venues = 50

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = buenosaires_grouped['Neighborhood']

for ind in np.arange(buenosaires_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(buenosaires_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood   1st Most Common Venue 2nd Most Common Venue  \
0    AGRONOMIA            Soccer Field         Train Station   
1      ALMAGRO  Argentinian Restaurant        Ice Cream Shop   
2    BALVANERA                    Café                 Hotel   
3     BARRACAS  Argentinian Restaurant                  Café   
4     BELGRANO                    Café             BBQ Joint   

  3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0           Snack Place           Pizza Place            Intersection   
1           Pizza Place                  Café                     Bar   
2           Pizza Place   Japanese Restaurant    Fast Food Restaurant   
3        Clothing Store         Auto Workshop      Athletics & Sports   
4           Pizza Place    Italian Restaurant  Argentinian Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                  Café           Sports Club         Garden Center   
1         Indie Theater                   Gym            Restaurant   
2                   Gym           Coffee Shop                   Bar   
3                Bakery                 Plaza                  Park   
4        Ice Cream Shop           Coffee Shop     French Restaurant   

  9th Most Common Venue 10th Most Common Venue 11th Most Common Venue  \
0             BBQ Joint                  Trail             Restaurant   
1    Italian Restaurant                  Hotel           Concert Hall   
2               Theater                 Bakery      Electronics Store   
3        Soccer Stadium            Pizza Place           Soccer Field   
4                Bakery          Grocery Store       Sushi Restaurant   

  12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
0     Athletics & Sports     Falafel Restaurant                Exhibit   
1            Coffee Shop  Performing Arts Venue         Sandwich Place   
2              BBQ Joint    Peruvian Restaurant               Pharmacy   
3            Flower Shop      Electronics Store                    Gym   
4            Supermarket            Salad Place              Speakeasy   

  15th Most Common Venue 16th Most Common Venue 17th Most Common Venue  \
0          Women's Store         Farmers Market          Event Service   
1            Cheese Shop   Fast Food Restaurant     Spanish Restaurant   
2    Arts & Crafts Store         Sandwich Place           Concert Hall   
3         Farmers Market   Fast Food Restaurant          Women's Store   
4                  Plaza               Beer Bar           Cocktail Bar   

  18th Most Common Venue 19th Most Common Venue 20th Most Common Venue  \
0   Fast Food Restaurant            Fish Market            Flea Market   
1               Pharmacy           Soccer Field            Flower Shop   
2                Brewery      Convenience Store              Nightclub   
3                Exhibit            Fish Market            Flea Market   
4               Tea Room         Sandwich Place                  Hotel   

  21th Most Common Venue         22th Most Common Venue  \
0            Event Space    Eastern European Restaurant   
1           Dessert Shop  Paper / Office Supplies Store   
2          Indie Theater                    Music Venue   
3                   Food             Falafel Restaurant   
4     Athletics & Sports               Asian Restaurant   

        23th Most Common Venue 24th Most Common Venue  \
0           English Restaurant    Empanada Restaurant   
1  Eastern European Restaurant                 Church   
2                 Burger Joint      Kosher Restaurant   
3           English Restaurant            Event Space   
4          Peruvian Restaurant                 Bistro   

      25th Most Common Venue 26th Most Common Venue  \
0          Electronics Store                   Food   
1   Bike Rental / Bike Share    Empanada Restaurant   
2                Comedy Club             Restaurant   
3              Event Service             Food Court   
4  L

<a id='item4'></a>

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [45]:
# kclusters = 5

kclusters = 10

buenosaires_grouped_clustering = buenosaires_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(buenosaires_grouped_clustering)

# check cluster labels generated for first 10 rows in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 2, 2, 2, 2, 1, 2, 2, 2], dtype=int32)

In [46]:
# check all labels
kmeans.labels_

array([2, 2, 2, 2, 2, 2, 1, 2, 2, 2, 2, 8, 2, 2, 0, 0, 2, 8, 0, 2, 2, 5,
       2, 9, 2, 4, 2, 2, 2, 2, 3, 2, 2, 1, 2, 2, 2, 2, 3, 0, 2, 2, 3, 3,
       6, 2, 7, 2], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [47]:
# match column names
# neighborhoods_venues_sorted.rename(columns={"Neighborhood":"AREA_NAME"}, inplace=True)
neighborhoods_venues_sorted

Neighborhood   1st Most Common Venue          2nd Most Common Venue  \
0           AGRONOMIA            Soccer Field                  Train Station   
1             ALMAGRO  Argentinian Restaurant                 Ice Cream Shop   
2           BALVANERA                    Café                          Hotel   
3            BARRACAS  Argentinian Restaurant                           Café   
4            BELGRANO                    Café                      BBQ Joint   
5                BOCA                 Theater                       Bus Stop   
6               BOEDO  Argentinian Restaurant                   Soccer Field   
7           CABALLITO                    Café                 Ice Cream Shop   
8           CHACARITA                    Café                    Pizza Place   
9             COGHLAN                    Café                    Pizza Place   
10         COLEGIALES  Argentinian Restaurant                    Pizza Place   
11       CONSTITUCION                Bus Stop                           Café   
12             FLORES             Pizza Place                 Ice Cream Shop   
13           FLORESTA  Argentinian Restaurant                  Deli / Bodega   
14            LINIERS             Pizza Place         Argentinian Restaurant   
15          MATADEROS             Pizza Place  Paper / Office Supplies Store   
16          MONSERRAT                    Café             Spanish Restaurant   
17       MONTE CASTRO                Bus Stop                    Pizza Place   
18      NUEVA POMPEYA             Pizza Place                  Grocery Store   
19              NUÑEZ            Soccer Field                     Restaurant   
20            PALERMO  Argentinian Restaurant             Italian Restaurant   
21  PARQUE AVELLANEDA                    Park                     Toll Booth   
22   PARQUE CHACABUCO          Ice Cream Shop                       Pharmacy   
23        PARQUE CHAS                   Plaza                  Grocery Store   
24   PARQUE PATRICIOS             Pizza Place                           Park   
25           PATERNAL             Art Gallery           Arts & Entertainment   
26      PUERTO MADERO              Food Truck                      Hotel Bar   
27           RECOLETA                   Hotel                    Coffee Shop   
28             RETIRO                   Hotel                  Boat or Ferry   
29           SAAVEDRA          Ice Cream Shop                          Plaza   
30      SAN CRISTOBAL                Bus Stop                 Ice Cream Shop   
31        SAN NICOLAS             Coffee Shop                          Hotel   
32          SAN TELMO  Argentinian Restaurant                 Ice Cream Shop   
33    VELEZ SARSFIELD  Argentinian Restaurant                      BBQ Joint   
34          VERSALLES     Sporting Goods Shop                 Hardware Store   
35       VILLA CRESPO             Pizza Place         Argentinian Restaurant   
36   VILLA DEL PARQUE             Pizza Place         Argentinian Restaurant   
37       VILLA DEVOTO             Coffee Shop                 Ice Cream Shop   
38  VILLA GRAL. MITRE                   Plaza                 Sandwich Place   
39       VILLA LUGANO             Pizza Place                 Ice Cream Shop   
40         VILLA LURO  Argentinian Restaurant                      BBQ Joint   
41      VILLA ORTUZAR               BBQ Joint                    Supermarket   
42   VILLA PUEYRREDON          Ice Cream Shop                          Plaza   
43         VILLA REAL                Bus Stop                   Tennis Court   
44    VILLA RIACHUELO               Racetrack                  Go Kart Track   
45   VILLA SANTA RITA          Ice Cream Shop                            Gym   
46      VILLA SOLDATI      Light Rail Station                 Rental Service   
47      VILLA URQUIZA                  Bakery                 Ice Cream Shop   

     3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0           

In [48]:
neighborhoods_venues_sorted.shape

(48, 51)

In [49]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

In [50]:
neighborhoods_venues_sorted.shape

(48, 52)

In [51]:
neighborhoods_venues_sorted

Cluster Labels       Neighborhood   1st Most Common Venue  \
0                2          AGRONOMIA            Soccer Field   
1                2            ALMAGRO  Argentinian Restaurant   
2                2          BALVANERA                    Café   
3                2           BARRACAS  Argentinian Restaurant   
4                2           BELGRANO                    Café   
5                2               BOCA                 Theater   
6                1              BOEDO  Argentinian Restaurant   
7                2          CABALLITO                    Café   
8                2          CHACARITA                    Café   
9                2            COGHLAN                    Café   
10               2         COLEGIALES  Argentinian Restaurant   
11               8       CONSTITUCION                Bus Stop   
12               2             FLORES             Pizza Place   
13               2           FLORESTA  Argentinian Restaurant   
14               0            LINIERS             Pizza Place   
15               0          MATADEROS             Pizza Place   
16               2          MONSERRAT                    Café   
17               8       MONTE CASTRO                Bus Stop   
18               0      NUEVA POMPEYA             Pizza Place   
19               2              NUÑEZ            Soccer Field   
20               2            PALERMO  Argentinian Restaurant   
21               5  PARQUE AVELLANEDA                    Park   
22               2   PARQUE CHACABUCO          Ice Cream Shop   
23               9        PARQUE CHAS                   Plaza   
24               2   PARQUE PATRICIOS             Pizza Place   
25               4           PATERNAL             Art Gallery   
26               2      PUERTO MADERO              Food Truck   
27               2           RECOLETA                   Hotel   
28               2             RETIRO                   Hotel   
29               2           SAAVEDRA          Ice Cream Shop   
30               3      SAN CRISTOBAL                Bus Stop   
31               2        SAN NICOLAS             Coffee Shop   
32               2          SAN TELMO  Argentinian Restaurant   
33               1    VELEZ SARSFIELD  Argentinian Restaurant   
34               2          VERSALLES     Sporting Goods Shop   
35               2       VILLA CRESPO             Pizza Place   
36               2   VILLA DEL PARQUE             Pizza Place   
37               2       VILLA DEVOTO             Coffee Shop   
38               3  VILLA GRAL. MITRE                   Plaza   
39               0       VILLA LUGANO             Pizza Place   
40               2         VILLA LURO  Argentinian Restaurant   
41               2      VILLA ORTUZAR               BBQ Joint   
42               3   VILLA PUEYRREDON          Ice Cream Shop   
43               3         VILLA REAL                Bus Stop   
44               6    VILLA RIACHUELO               Racetrack   
45               2   VILLA SANTA RITA          Ice Cream Shop   
46               7      VILLA SOLDATI      Light Rail Station   
47               2      VILLA URQUIZA                  Bakery   

            2nd Most Common Venue   3rd Most Common Venue  \
0                   Train Station             Snack Place   
1                  Ice Cream Shop             Pizza Place   
2                           Hotel             Pizza Place   
3                            Café          Clothing Store   
4                       BBQ Joint             Pizza Place   
5                        Bus Stop             Pizza Place   
6                    Soccer Field             Pizza Place   
7                  Ice Cream Shop             Coffee Shop   
8                     Pizza Place                  Bakery   
9                     Pizza Place                 Brewery   
10                    Pizza Place                  Bakery   
11                           Café  Argentinian Restaurant   
12                 Ice Cr

In [52]:
buenosaires_merged = neighborhoods # buenosaires_data

# merge buenosaires_grouped with buenosaires_data to add latitude/longitude for each neighborhood
buenosaires_merged = buenosaires_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='neighborhood')

In [53]:
buenosaires_merged.shape

(48, 57)

In [54]:
buenosaires_merged

# We can see in the full table that some areas/neighborhoods do not have venues and then can't be assigned to a cluster with the same criteria than others

neighborhood commune          area   latitude  longitude  \
0           CHACARITA      15  3.115707e+06 -34.588065 -58.452682   
1            PATERNAL      15  2.229829e+06 -34.596378 -58.467534   
2        VILLA CRESPO      15  3.615978e+06 -34.598142 -58.441151   
3    VILLA DEL PARQUE      11  3.399596e+06 -34.605902 -58.490092   
4             ALMAGRO       5  4.050752e+06 -34.609894 -58.422626   
5           CABALLITO       6  6.851029e+06 -34.616656 -58.444730   
6    VILLA SANTA RITA      11  2.153691e+06 -34.616378 -58.483203   
7        MONTE CASTRO      10  2.627481e+06 -34.618788 -58.507137   
8          VILLA REAL      10  1.334146e+06 -34.619209 -58.524234   
9              FLORES       7  8.590784e+06 -34.635346 -58.454119   
10           FLORESTA      10  2.320641e+06 -34.627832 -58.484752   
11       CONSTITUCION       1  2.101995e+06 -34.625788 -58.383635   
12      SAN CRISTOBAL       3  2.043711e+06 -34.624258 -58.401857   
13              BOEDO       5  2.609851e+06 -34.630421 -58.419142   
14    VELEZ SARSFIELD      10  2.400518e+06 -34.631335 -58.492920   
15         VILLA LURO      10  2.566937e+06 -34.635048 -58.502094   
16   PARQUE PATRICIOS       4  3.743440e+06 -34.637918 -58.401659   
17          MATADEROS       9  7.398179e+06 -34.658959 -58.502296   
18       VILLA LUGANO       8  9.296142e+06 -34.674654 -58.476584   
19          SAN TELMO       1  1.232270e+06 -34.622559 -58.370440   
20           SAAVEDRA      12  5.538677e+06 -34.554314 -58.489032   
21            COGHLAN      12  1.279951e+06 -34.560191 -58.475025   
22      VILLA URQUIZA      12  5.449059e+06 -34.571961 -58.488561   
23         COLEGIALES      13  2.289774e+06 -34.574640 -58.451647   
24          BALVANERA       3  4.342280e+06 -34.609323 -58.403159   
25  VILLA GRAL. MITRE      11  2.162275e+06 -34.610508 -58.469442   
26        PARQUE CHAS      15  1.385412e+06 -34.585424 -58.479804   
27          AGRONOMIA      15  2.122169e+06 -34.592245 -58.489716   
28      VILLA ORTUZAR      15  1.853802e+06 -34.581545 -58.469606   
29           BARRACAS       4  7.953453e+06 -34.644455 -58.386347   
30  PARQUE AVELLANEDA       9  4.732708e+06 -34.649714 -58.477852   
31   PARQUE CHACABUCO       7  3.832117e+06 -34.637175 -58.438935   
32      NUEVA POMPEYA       4  4.951511e+06 -34.650074 -58.417980   
33            PALERMO      14  1.584587e+07 -34.574395 -58.420942   
34    VILLA RIACHUELO       8  4.232596e+06 -34.692861 -58.463825   
35      VILLA SOLDATI       8  8.688164e+06 -34.667878 -58.447252   
36   VILLA PUEYRREDON      12  3.303240e+06 -34.581609 -58.502165   
37       VILLA DEVOTO      11  6.404481e+06 -34.600742 -58.513322   
38            LINIERS       9  4.374419e+06 -34.644845 -58.516329   
39          VERSALLES      10  1.406834e+06 -34.629173 -58.519596   
40      PUERTO MADERO       1  5.040971e+06 -34.610079 -58.354678   
41          MONSERRAT       1  2.198622e+06 -34.612331 -58.379343   
42        SAN NICOLAS       1  2.289008e+06 -34.603807 -58.380328   
43           BELGRANO      13  7.999240e+06 -34.553346 -58.449426   
44           RECOLETA       2  6.317265e+06 -34.584014 -58.393348   
45             RETIRO       1  4.512711e+06 -34.588388 -58.371290   
46              NUÑEZ      13  4.424199e+06 -34.542709 -58.462614   
47               BOCA       4  5.036240e+06 -34.633872 -58.352904   

         radius  Cluster Labels   1st Most Common Venue  \
0    746.903749               2                    Café   
1    631.861814               4             Art Gallery   
2    804.635501               2             Pizza Place   
3    780.189244               2             Pizza Place   
4    851.636306               2  Argentinian Restaurant   
5   1107.552259               2                    Café   
6    620.980560               2          Ice Cream Shop   
7    685.892645               8                Bus Stop   
8    488.751406               3                Bus Stop   
9   1240.231422               2      

In [55]:
# The neighbourhoods (areas) that did not report any venue don't belong to any category
# Areas without venues will not be considered for this study
buenosaires_merged.dropna(inplace= True)

buenosaires_merged

# All neighborhoods have venues to be clustered (OK)

neighborhood commune          area   latitude  longitude  \
0           CHACARITA      15  3.115707e+06 -34.588065 -58.452682   
1            PATERNAL      15  2.229829e+06 -34.596378 -58.467534   
2        VILLA CRESPO      15  3.615978e+06 -34.598142 -58.441151   
3    VILLA DEL PARQUE      11  3.399596e+06 -34.605902 -58.490092   
4             ALMAGRO       5  4.050752e+06 -34.609894 -58.422626   
5           CABALLITO       6  6.851029e+06 -34.616656 -58.444730   
6    VILLA SANTA RITA      11  2.153691e+06 -34.616378 -58.483203   
7        MONTE CASTRO      10  2.627481e+06 -34.618788 -58.507137   
8          VILLA REAL      10  1.334146e+06 -34.619209 -58.524234   
9              FLORES       7  8.590784e+06 -34.635346 -58.454119   
10           FLORESTA      10  2.320641e+06 -34.627832 -58.484752   
11       CONSTITUCION       1  2.101995e+06 -34.625788 -58.383635   
12      SAN CRISTOBAL       3  2.043711e+06 -34.624258 -58.401857   
13              BOEDO       5  2.609851e+06 -34.630421 -58.419142   
14    VELEZ SARSFIELD      10  2.400518e+06 -34.631335 -58.492920   
15         VILLA LURO      10  2.566937e+06 -34.635048 -58.502094   
16   PARQUE PATRICIOS       4  3.743440e+06 -34.637918 -58.401659   
17          MATADEROS       9  7.398179e+06 -34.658959 -58.502296   
18       VILLA LUGANO       8  9.296142e+06 -34.674654 -58.476584   
19          SAN TELMO       1  1.232270e+06 -34.622559 -58.370440   
20           SAAVEDRA      12  5.538677e+06 -34.554314 -58.489032   
21            COGHLAN      12  1.279951e+06 -34.560191 -58.475025   
22      VILLA URQUIZA      12  5.449059e+06 -34.571961 -58.488561   
23         COLEGIALES      13  2.289774e+06 -34.574640 -58.451647   
24          BALVANERA       3  4.342280e+06 -34.609323 -58.403159   
25  VILLA GRAL. MITRE      11  2.162275e+06 -34.610508 -58.469442   
26        PARQUE CHAS      15  1.385412e+06 -34.585424 -58.479804   
27          AGRONOMIA      15  2.122169e+06 -34.592245 -58.489716   
28      VILLA ORTUZAR      15  1.853802e+06 -34.581545 -58.469606   
29           BARRACAS       4  7.953453e+06 -34.644455 -58.386347   
30  PARQUE AVELLANEDA       9  4.732708e+06 -34.649714 -58.477852   
31   PARQUE CHACABUCO       7  3.832117e+06 -34.637175 -58.438935   
32      NUEVA POMPEYA       4  4.951511e+06 -34.650074 -58.417980   
33            PALERMO      14  1.584587e+07 -34.574395 -58.420942   
34    VILLA RIACHUELO       8  4.232596e+06 -34.692861 -58.463825   
35      VILLA SOLDATI       8  8.688164e+06 -34.667878 -58.447252   
36   VILLA PUEYRREDON      12  3.303240e+06 -34.581609 -58.502165   
37       VILLA DEVOTO      11  6.404481e+06 -34.600742 -58.513322   
38            LINIERS       9  4.374419e+06 -34.644845 -58.516329   
39          VERSALLES      10  1.406834e+06 -34.629173 -58.519596   
40      PUERTO MADERO       1  5.040971e+06 -34.610079 -58.354678   
41          MONSERRAT       1  2.198622e+06 -34.612331 -58.379343   
42        SAN NICOLAS       1  2.289008e+06 -34.603807 -58.380328   
43           BELGRANO      13  7.999240e+06 -34.553346 -58.449426   
44           RECOLETA       2  6.317265e+06 -34.584014 -58.393348   
45             RETIRO       1  4.512711e+06 -34.588388 -58.371290   
46              NUÑEZ      13  4.424199e+06 -34.542709 -58.462614   
47               BOCA       4  5.036240e+06 -34.633872 -58.352904   

         radius  Cluster Labels   1st Most Common Venue  \
0    746.903749               2                    Café   
1    631.861814               4             Art Gallery   
2    804.635501               2             Pizza Place   
3    780.189244               2             Pizza Place   
4    851.636306               2  Argentinian Restaurant   
5   1107.552259               2                    Café   
6    620.980560               2          Ice Cream Shop   
7    685.892645               8                Bus Stop   
8    488.751406               3                Bus Stop   
9   1240.231422               2      

In [56]:
# recast to int32 the cluster label column after join operation
buenosaires_merged['Cluster Labels'] = buenosaires_merged['Cluster Labels'].astype(int)

buenosaires_merged

neighborhood commune          area   latitude  longitude  \
0           CHACARITA      15  3.115707e+06 -34.588065 -58.452682   
1            PATERNAL      15  2.229829e+06 -34.596378 -58.467534   
2        VILLA CRESPO      15  3.615978e+06 -34.598142 -58.441151   
3    VILLA DEL PARQUE      11  3.399596e+06 -34.605902 -58.490092   
4             ALMAGRO       5  4.050752e+06 -34.609894 -58.422626   
5           CABALLITO       6  6.851029e+06 -34.616656 -58.444730   
6    VILLA SANTA RITA      11  2.153691e+06 -34.616378 -58.483203   
7        MONTE CASTRO      10  2.627481e+06 -34.618788 -58.507137   
8          VILLA REAL      10  1.334146e+06 -34.619209 -58.524234   
9              FLORES       7  8.590784e+06 -34.635346 -58.454119   
10           FLORESTA      10  2.320641e+06 -34.627832 -58.484752   
11       CONSTITUCION       1  2.101995e+06 -34.625788 -58.383635   
12      SAN CRISTOBAL       3  2.043711e+06 -34.624258 -58.401857   
13              BOEDO       5  2.609851e+06 -34.630421 -58.419142   
14    VELEZ SARSFIELD      10  2.400518e+06 -34.631335 -58.492920   
15         VILLA LURO      10  2.566937e+06 -34.635048 -58.502094   
16   PARQUE PATRICIOS       4  3.743440e+06 -34.637918 -58.401659   
17          MATADEROS       9  7.398179e+06 -34.658959 -58.502296   
18       VILLA LUGANO       8  9.296142e+06 -34.674654 -58.476584   
19          SAN TELMO       1  1.232270e+06 -34.622559 -58.370440   
20           SAAVEDRA      12  5.538677e+06 -34.554314 -58.489032   
21            COGHLAN      12  1.279951e+06 -34.560191 -58.475025   
22      VILLA URQUIZA      12  5.449059e+06 -34.571961 -58.488561   
23         COLEGIALES      13  2.289774e+06 -34.574640 -58.451647   
24          BALVANERA       3  4.342280e+06 -34.609323 -58.403159   
25  VILLA GRAL. MITRE      11  2.162275e+06 -34.610508 -58.469442   
26        PARQUE CHAS      15  1.385412e+06 -34.585424 -58.479804   
27          AGRONOMIA      15  2.122169e+06 -34.592245 -58.489716   
28      VILLA ORTUZAR      15  1.853802e+06 -34.581545 -58.469606   
29           BARRACAS       4  7.953453e+06 -34.644455 -58.386347   
30  PARQUE AVELLANEDA       9  4.732708e+06 -34.649714 -58.477852   
31   PARQUE CHACABUCO       7  3.832117e+06 -34.637175 -58.438935   
32      NUEVA POMPEYA       4  4.951511e+06 -34.650074 -58.417980   
33            PALERMO      14  1.584587e+07 -34.574395 -58.420942   
34    VILLA RIACHUELO       8  4.232596e+06 -34.692861 -58.463825   
35      VILLA SOLDATI       8  8.688164e+06 -34.667878 -58.447252   
36   VILLA PUEYRREDON      12  3.303240e+06 -34.581609 -58.502165   
37       VILLA DEVOTO      11  6.404481e+06 -34.600742 -58.513322   
38            LINIERS       9  4.374419e+06 -34.644845 -58.516329   
39          VERSALLES      10  1.406834e+06 -34.629173 -58.519596   
40      PUERTO MADERO       1  5.040971e+06 -34.610079 -58.354678   
41          MONSERRAT       1  2.198622e+06 -34.612331 -58.379343   
42        SAN NICOLAS       1  2.289008e+06 -34.603807 -58.380328   
43           BELGRANO      13  7.999240e+06 -34.553346 -58.449426   
44           RECOLETA       2  6.317265e+06 -34.584014 -58.393348   
45             RETIRO       1  4.512711e+06 -34.588388 -58.371290   
46              NUÑEZ      13  4.424199e+06 -34.542709 -58.462614   
47               BOCA       4  5.036240e+06 -34.633872 -58.352904   

         radius  Cluster Labels   1st Most Common Venue  \
0    746.903749               2                    Café   
1    631.861814               4             Art Gallery   
2    804.635501               2             Pizza Place   
3    780.189244               2             Pizza Place   
4    851.636306               2  Argentinian Restaurant   
5   1107.552259               2                    Café   
6    620.980560               2          Ice Cream Shop   
7    685.892645               8                Bus Stop   
8    488.751406               3                Bus Stop   
9   1240.231422               2      

Finally, let's visualize the resulting clusters

In [57]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(buenosaires_merged['latitude'], buenosaires_merged['longitude'], buenosaires_merged['neighborhood'], buenosaires_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# RESULTS SECTION

<a id='item5'></a>

## 5. Examine Clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

#### Cluster 1

In [58]:
buenosaires_merged.loc[buenosaires_merged['Cluster Labels'] == 0, buenosaires_merged.columns[[0] + list(range(5, buenosaires_merged.shape[1]))]]

neighborhood       radius  Cluster Labels 1st Most Common Venue  \
17      MATADEROS  1150.929548               0           Pizza Place   
18   VILLA LUGANO  1290.142583               0           Pizza Place   
32  NUEVA POMPEYA   941.575600               0           Pizza Place   
38        LINIERS   885.006588               0           Pizza Place   

            2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
17  Paper / Office Supplies Store                  Café          Dessert Shop   
18                 Ice Cream Shop          Dessert Shop        Shipping Store   
32                  Grocery Store          Soccer Field  Fast Food Restaurant   
38         Argentinian Restaurant                 Plaza  Gym / Fitness Center   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
17          Ice Cream Shop          Soccer Field             BBQ Joint   
18                Pharmacy  Gym / Fitness Center     Electronics Store   
32  Thrift / Vintage Store    Seafood Restaurant                 Plaza   
38               Bike Shop        Sandwich Place              Tea Room   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
17           Grocery Store              Pharmacy             Restaurant   
18  Argentinian Restaurant    Dim Sum Restaurant            Event Space   
32              Food Truck             Nightclub            Fish Market   
38        Basketball Court          Burger Joint              Rock Club   

   11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
17            Sports Club         Soccer Stadium          Deli / Bodega   
18      Food & Drink Shop                   Food            Flower Shop   
32     English Restaurant         Farmers Market     Falafel Restaurant   
38              BBQ Joint                    Gym            Coffee Shop   

   14th Most Common Venue 15th Most Common Venue       16th Most Common Venue  \
17              Gastropub          Event Service         Fast Food Restaurant   
18            Flea Market            Fish Market         Fast Food Restaurant   
32            Flea Market                Exhibit                  Event Space   
38         Ice Cream Shop           Dessert Shop  Eastern European Restaurant   

   17th Most Common Venue 18th Most Common Venue 19th Most Common Venue  \
17         Farmers Market     Falafel Restaurant                Exhibit   
18         Farmers Market     Falafel Restaurant                Exhibit   
32          Event Service          Women's Store      Electronics Store   
38                Exhibit                   Food            Flower Shop   

   20th Most Common Venue 21th Most Common Venue       22th Most Common Venue  \
17            Event Space            Fish Market            Electronics Store   
18          Event Service                  Diner           English Restaurant   
32    Empanada Restaurant                   Food  Eastern European Restaurant   
38            Flea Market            Fish Market         Fast Food Restaurant   

   23th Most Common Venue 24th Most Common Venue 25th Most Common Venue  \
17     English Restaurant    Empanada Restaurant            Flower Shop   
18           Dance Studio    Empanada Restaurant           Food Service   
32            Dry Cleaner                Dog Run                  Diner   
38         Farmers Market       Department Store     Falafel Restaurant   

         26th Most Common Venue 27th Most Common Venue  \
17  Eastern European Restaurant            Dry Cleaner   
18                Deli / Bodega       Department Store   
32           Dim Sum Restaurant           Dessert Shop   
38                  Event Space            Dry Cleaner   

         28th Most Common Venue 29th Most Common Venue 30th Most Common Venue  \
17                      Dog Run                  Diner     Dim Sum Restaurant   
18  Eastern European Restaurant            Dry Cleaner                Dog Run   
32             De

#### Cluster 2

In [59]:
buenosaires_merged.loc[buenosaires_merged['Cluster Labels'] == 1, buenosaires_merged.columns[[0] + list(range(5, buenosaires_merged.shape[1]))]]

neighborhood      radius  Cluster Labels   1st Most Common Venue  \
13            BOEDO  683.587596               1  Argentinian Restaurant   
14  VELEZ SARSFIELD  655.599842               1  Argentinian Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
13          Soccer Field           Pizza Place              Pharmacy   
14             BBQ Joint   Sporting Goods Shop                   Gym   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
13     Convenience Store              Bus Stop        Ice Cream Shop   
14          Soccer Field           Sports Club              Bus Stop   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
13                Bakery            Restaurant            Cheese Shop   
14          Tennis Court        Sandwich Place          Deli / Bodega   

   11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
13                   Café                Brewery                Stadium   
14            Pizza Place                  Diner                Exhibit   

   14th Most Common Venue 15th Most Common Venue 16th Most Common Venue  \
13          Metro Station         Breakfast Spot              BBQ Joint   
14                   Food            Flower Shop           Dance Studio   

   17th Most Common Venue 18th Most Common Venue 19th Most Common Venue  \
13           Intersection          Auto Workshop          Event Service   
14            Flea Market            Fish Market       Department Store   

   20th Most Common Venue 21th Most Common Venue 22th Most Common Venue  \
13                   Food            Flower Shop            Flea Market   
14   Fast Food Restaurant         Farmers Market     Falafel Restaurant   

   23th Most Common Venue 24th Most Common Venue 25th Most Common Venue  \
13            Fish Market   Fast Food Restaurant         Farmers Market   
14            Event Space                Dog Run          Event Service   

   26th Most Common Venue 27th Most Common Venue 28th Most Common Venue  \
13     Falafel Restaurant                Exhibit            Event Space   
14     English Restaurant             Food Court    Empanada Restaurant   

   29th Most Common Venue 30th Most Common Venue       31th Most Common Venue  \
13                    Gym          Historic Site               History Museum   
14      Electronics Store           Dessert Shop  Eastern European Restaurant   

   32th Most Common Venue 33th Most Common Venue 34th Most Common Venue  \
13    Empanada Restaurant             Hobby Shop      Electronics Store   
14     Dim Sum Restaurant            Dry Cleaner      Food & Drink Shop   

         35th Most Common Venue 36th Most Common Venue 37th Most Common Venue  \
13  Eastern European Restaurant            Dry Cleaner                 Hostel   
14                Women's Store           Food Service             Food Truck   

   38th Most Common Venue 39th Most Common Venue 40th Most Common Venue  \
13                Dog Run                  Diner          Hot Dog Joint   
14          Hot Dog Joint                 Hostel             Hobby Shop   

   41th Most Common Venue 42th Most Common Venue 43th Most Common Venue  \
13     English Restaurant             Food Court      Food & Drink Shop   
14         History Museum          Historic Site         Hardware Store   

   44th Most Common Venue 45th Most Common Venue 46th Most Common Venue  \
13         Hardware Store          Grocery Store           Gourmet Shop   
14        Harbor / Marina         Gymnastics Gym   Gym / Fitness Center   

   47th Most Common Venue 48th Most Common Venue 49th Most Common Venue  \
13          Go Kart Track              Gift Shop      German Restaurant   
14          Grocery Store           Gourmet Shop          Go Kart Track   

   50th Most Common Venue  
13  General Entertainment  
14              Gift Shop

#### Cluster 3

In [60]:
buenosaires_merged.loc[buenosaires_merged['Cluster Labels'] == 2, buenosaires_merged.columns[[0] + list(range(5, buenosaires_merged.shape[1]))]]

neighborhood       radius  Cluster Labels   1st Most Common Venue  \
0          CHACARITA   746.903749               2                    Café   
2       VILLA CRESPO   804.635501               2             Pizza Place   
3   VILLA DEL PARQUE   780.189244               2             Pizza Place   
4            ALMAGRO   851.636306               2  Argentinian Restaurant   
5          CABALLITO  1107.552259               2                    Café   
6   VILLA SANTA RITA   620.980560               2          Ice Cream Shop   
9             FLORES  1240.231422               2             Pizza Place   
10          FLORESTA   644.599973               2  Argentinian Restaurant   
15        VILLA LURO   677.944156               2  Argentinian Restaurant   
16  PARQUE PATRICIOS   818.694297               2             Pizza Place   
19         SAN TELMO   469.720260               2  Argentinian Restaurant   
20          SAAVEDRA   995.839480               2          Ice Cream Shop   
21           COGHLAN   478.721643               2                    Café   
22     VILLA URQUIZA   987.750093               2                  Bakery   
23        COLEGIALES   640.298739               2  Argentinian Restaurant   
24         BALVANERA   881.749562               2                    Café   
27         AGRONOMIA   616.419466               2            Soccer Field   
28     VILLA ORTUZAR   576.126705               2               BBQ Joint   
29          BARRACAS  1193.340001               2  Argentinian Restaurant   
31  PARQUE CHACABUCO   828.334386               2          Ice Cream Shop   
33           PALERMO  1684.396728               2  Argentinian Restaurant   
37      VILLA DEVOTO  1070.849142               2             Coffee Shop   
39         VERSALLES   501.889018               2     Sporting Goods Shop   
40     PUERTO MADERO   950.043348               2              Food Truck   
41         MONSERRAT   627.424692               2                    Café   
42       SAN NICOLAS   640.191558               2             Coffee Shop   
43          BELGRANO  1196.769977               2                    Café   
44          RECOLETA  1063.532730               2                   Hotel   
45            RETIRO   898.886967               2                   Hotel   
46             NUÑEZ   890.027994               2            Soccer Field   
47              BOCA   949.597485               2                 Theater   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0              Pizza Place                Bakery            Restaurant   
2   Argentinian Restaurant                  Café        Clothing Store   
3   Argentinian Restaurant              Pharmacy                 Plaza   
4           Ice Cream Shop           Pizza Place                  Café   
5           Ice Cream Shop           Coffee Shop                Bakery   
6                      Gym           Sports Club          Soccer Field   
9           Ice Cream Shop                  Café            Restaurant   
10           Deli / Bodega            Restaurant              Bus Stop   
15               BBQ Joint           Pizza Place        Ice Cream Shop   
16                    Park        Ice Cream Shop                  Café   
19          Ice Cream Shop                  Café            Restaurant   
20                   Plaza                  Park   Sporting Goods Shop   
21             Pizza Place               Brewery  Gym / Fitness Center   
22          Ice Cream Shop           Pizza Place           Coffee Shop   
23             Pizza Place                Bakery              Beer Bar   
24                   Hotel           Pizza Place   Japanese Restaurant   
27           Train Station           Snack Place           Pizza Place   
28             Supermarket              Pharmacy                Bakery   
29                    Café        Clothing Store         Auto Workshop   
31                Pharmacy     Korean Restaurant           Pizz

#### Cluster 4

In [61]:
buenosaires_merged.loc[buenosaires_merged['Cluster Labels'] == 3, buenosaires_merged.columns[[0] + list(range(5, buenosaires_merged.shape[1]))]]

neighborhood      radius  Cluster Labels 1st Most Common Venue  \
8          VILLA REAL  488.751406               3              Bus Stop   
12      SAN CRISTOBAL  604.917406               3              Bus Stop   
25  VILLA GRAL. MITRE  622.216899               3                 Plaza   
36   VILLA PUEYRREDON  769.053157               3        Ice Cream Shop   

   2nd Most Common Venue   3rd Most Common Venue 4th Most Common Venue  \
8           Tennis Court                   Plaza           Bus Station   
12        Ice Cream Shop             Pizza Place               Theater   
25        Sandwich Place      Italian Restaurant     Outdoor Sculpture   
36                 Plaza  Argentinian Restaurant              Bus Stop   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
8         History Museum       Motorcycle Shop                Bakery   
12          Tennis Court             BBQ Joint        Breakfast Spot   
25                  Café           Supermarket              Bus Stop   
36          Tennis Court         Train Station     Electronics Store   

   8th Most Common Venue      9th Most Common Venue  10th Most Common Venue  \
8     Athletics & Sports                  Rock Club                     Gym   
12                 Plaza  Middle Eastern Restaurant  Furniture / Home Store   
25          Tennis Court               Intersection             Pizza Place   
36             BBQ Joint             Shop & Service             Sports Club   

   11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
8    Fast Food Restaurant                Exhibit     Falafel Restaurant   
12            Supermarket       Sushi Restaurant           Soccer Field   
25         Soccer Stadium         Ice Cream Shop            Fish Market   
36               Pharmacy                 Tunnel           Dessert Shop   

   14th Most Common Venue 15th Most Common Venue 16th Most Common Venue  \
8          Farmers Market          Women's Store            Event Space   
12      Convenience Store        Cultural Center               Pharmacy   
25          Event Service         Farmers Market     Falafel Restaurant   
36            Bus Station            Event Space            Fish Market   

   17th Most Common Venue 18th Most Common Venue 19th Most Common Venue  \
8             Flea Market            Flower Shop                   Food   
12           Dessert Shop    Japanese Restaurant   Gym / Fitness Center   
25            Flea Market                Exhibit            Event Space   
36            Flea Market   Fast Food Restaurant            Flower Shop   

   20th Most Common Venue 21th Most Common Venue 22th Most Common Venue  \
8             Fish Market    Empanada Restaurant          Event Service   
12                  Diner            Flea Market          Deli / Bodega   
25   Fast Food Restaurant          Women's Store     English Restaurant   
36         Farmers Market     Falafel Restaurant                Exhibit   

   23th Most Common Venue 24th Most Common Venue 25th Most Common Venue  \
8      English Restaurant             Food Court      Electronics Store   
12            Fish Market       Department Store   Fast Food Restaurant   
25                   Food    Empanada Restaurant      Electronics Store   
36          Hot Dog Joint          Event Service     English Restaurant   

         26th Most Common Venue 27th Most Common Venue  \
8   Eastern European Restaurant            Dry Cleaner   
12               Farmers Market     Falafel Restaurant   
25  Eastern European Restaurant            Dry Cleaner   
36          Empanada Restaurant      Food & Drink Shop   

         28th Most Common Venue 29th Most Common Venue 30th Most Common Venue  \
8                       Dog Run                  Diner     Dim Sum Restaurant   
12                  Event Space                Exhibit     Dim Sum Restaurant   
25                      Dog Run                  Diner     Dim Sum Restaurant   
36  Easter

#### Cluster 5

In [62]:
buenosaires_merged.loc[buenosaires_merged['Cluster Labels'] == 4,buenosaires_merged.columns[[0] + list(range(5, buenosaires_merged.shape[1]))]]

neighborhood      radius  Cluster Labels 1st Most Common Venue  \
1     PATERNAL  631.861814               4           Art Gallery   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1  Arts & Entertainment               Stadium             BBQ Joint   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
1                 Diner           Pizza Place           Flower Shop   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
1        Farmers Market  Fast Food Restaurant            Fish Market   

  11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
1            Flea Market          Women's Store                Exhibit   

  14th Most Common Venue 15th Most Common Venue 16th Most Common Venue  \
1                   Food      Food & Drink Shop             Food Court   

  17th Most Common Venue 18th Most Common Venue 19th Most Common Venue  \
1           Food Service     Falafel Restaurant     English Restaurant   

  20th Most Common Venue 21th Most Common Venue 22th Most Common Venue  \
1            Event Space          Event Service               Fountain   

  23th Most Common Venue 24th Most Common Venue       25th Most Common Venue  \
1    Empanada Restaurant      Electronics Store  Eastern European Restaurant   

  26th Most Common Venue 27th Most Common Venue 28th Most Common Venue  \
1            Dry Cleaner                Dog Run     Dim Sum Restaurant   

  29th Most Common Venue 30th Most Common Venue 31th Most Common Venue  \
1           Dessert Shop       Department Store          Deli / Bodega   

  32th Most Common Venue   33th Most Common Venue 34th Most Common Venue  \
1             Food Truck  Fruit & Vegetable Store      French Restaurant   

  35th Most Common Venue 36th Most Common Venue 37th Most Common Venue  \
1                    Gym              Hotel Bar                  Hotel   

  38th Most Common Venue 39th Most Common Venue 40th Most Common Venue  \
1          Hot Dog Joint                 Hostel             Hobby Shop   

  41th Most Common Venue 42th Most Common Venue 43th Most Common Venue  \
1         History Museum          Historic Site         Hardware Store   

  44th Most Common Venue 45th Most Common Venue 46th Most Common Venue  \
1        Harbor / Marina         Gymnastics Gym   Gym / Fitness Center   

  47th Most Common Venue 48th Most Common Venue 49th Most Common Venue  \
1          Grocery Store           Cupcake Shop           Gourmet Shop   

  50th Most Common Venue  
1          Go Kart Track

#### Cluster 6

In [63]:
buenosaires_merged.loc[buenosaires_merged['Cluster Labels'] == 5,buenosaires_merged.columns[[0] + list(range(5, buenosaires_merged.shape[1]))]]

neighborhood      radius  Cluster Labels 1st Most Common Venue  \
30  PARQUE AVELLANEDA  920.536878               5                  Park   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
30            Toll Booth                  Pool        Ice Cream Shop   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
30     Convenience Store     Food & Drink Shop              Bus Stop   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
30         Shopping Mall    Athletics & Sports            Supermarket   

   11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
30                    Gym          Women's Store                Exhibit   

   14th Most Common Venue 15th Most Common Venue 16th Most Common Venue  \
30     Falafel Restaurant         Farmers Market   Fast Food Restaurant   

   17th Most Common Venue 18th Most Common Venue 19th Most Common Venue  \
30            Fish Market            Flea Market            Flower Shop   

   20th Most Common Venue 21th Most Common Venue 22th Most Common Venue  \
30            Event Space      Electronics Store          Event Service   

   23th Most Common Venue 24th Most Common Venue       25th Most Common Venue  \
30     English Restaurant    Empanada Restaurant  Eastern European Restaurant   

   26th Most Common Venue 27th Most Common Venue 28th Most Common Venue  \
30            Dry Cleaner                Dog Run                  Diner   

   29th Most Common Venue 30th Most Common Venue 31th Most Common Venue  \
30     Dim Sum Restaurant           Dessert Shop       Department Store   

   32th Most Common Venue 33th Most Common Venue 34th Most Common Venue  \
30          Deli / Bodega                   Food             Food Truck   

   35th Most Common Venue 36th Most Common Venue 37th Most Common Venue  \
30             Food Court          Go Kart Track                  Hotel   

   38th Most Common Venue 39th Most Common Venue 40th Most Common Venue  \
30          Hot Dog Joint                 Hostel             Hobby Shop   

   41th Most Common Venue 42th Most Common Venue 43th Most Common Venue  \
30         History Museum          Historic Site         Hardware Store   

   44th Most Common Venue 45th Most Common Venue 46th Most Common Venue  \
30        Harbor / Marina         Gymnastics Gym   Gym / Fitness Center   

   47th Most Common Venue 48th Most Common Venue 49th Most Common Venue  \
30          Grocery Store           Gourmet Shop              Gift Shop   

   50th Most Common Venue  
30           Food Service

#### Cluster 7

In [64]:
buenosaires_merged.loc[buenosaires_merged['Cluster Labels'] == 6,buenosaires_merged.columns[[0] + list(range(5, buenosaires_merged.shape[1]))]]

neighborhood      radius  Cluster Labels 1st Most Common Venue  \
34  VILLA RIACHUELO  870.542006               6             Racetrack   

   2nd Most Common Venue   3rd Most Common Venue 4th Most Common Venue  \
34         Go Kart Track  Furniture / Home Store           Supermarket   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
34     Food & Drink Shop                  Food           Flower Shop   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
34           Flea Market           Fish Market   Fast Food Restaurant   

   11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
34         Farmers Market     Falafel Restaurant                Exhibit   

   14th Most Common Venue 15th Most Common Venue 16th Most Common Venue  \
34            Event Space          Event Service     English Restaurant   

   17th Most Common Venue 18th Most Common Venue 19th Most Common Venue  \
34           Food Service    Empanada Restaurant      Electronics Store   

         20th Most Common Venue 21th Most Common Venue 22th Most Common Venue  \
34  Eastern European Restaurant            Dry Cleaner                Dog Run   

   23th Most Common Venue 24th Most Common Venue 25th Most Common Venue  \
34                  Diner     Dim Sum Restaurant           Dessert Shop   

   26th Most Common Venue 27th Most Common Venue 28th Most Common Venue  \
34       Department Store          Deli / Bodega           Dance Studio   

   29th Most Common Venue 30th Most Common Venue 31th Most Common Venue  \
34           Cupcake Shop        Cultural Center             Food Court   

   32th Most Common Venue 33th Most Common Venue 34th Most Common Venue  \
34          Women's Store             Food Truck                    Gym   

   35th Most Common Venue 36th Most Common Venue 37th Most Common Venue  \
34              Hotel Bar                  Hotel          Hot Dog Joint   

   38th Most Common Venue 39th Most Common Venue 40th Most Common Venue  \
34                 Hostel             Hobby Shop         History Museum   

   41th Most Common Venue 42th Most Common Venue 43th Most Common Venue  \
34          Historic Site         Hardware Store        Harbor / Marina   

   44th Most Common Venue 45th Most Common Venue 46th Most Common Venue  \
34         Gymnastics Gym   Gym / Fitness Center          Grocery Store   

   47th Most Common Venue 48th Most Common Venue 49th Most Common Venue  \
34       Cuban Restaurant           Gourmet Shop              Gift Shop   

   50th Most Common Venue  
34      German Restaurant

#### Cluster 8

In [65]:
buenosaires_merged.loc[buenosaires_merged['Cluster Labels'] == 7,buenosaires_merged.columns[[0] + list(range(5, buenosaires_merged.shape[1]))]]

neighborhood       radius  Cluster Labels 1st Most Common Venue  \
35  VILLA SOLDATI  1247.240834               7    Light Rail Station   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
35        Rental Service    Athletics & Sports         Train Station   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
35              Bus Stop                Bakery               Stadium   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
35           Flower Shop           Flea Market          Event Service   

   11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
35                   Food   Fast Food Restaurant      Food & Drink Shop   

   14th Most Common Venue 15th Most Common Venue 16th Most Common Venue  \
35         Farmers Market     Falafel Restaurant                Exhibit   

   17th Most Common Venue 18th Most Common Venue 19th Most Common Venue  \
35            Event Space            Fish Market          Women's Store   

   20th Most Common Venue 21th Most Common Venue 22th Most Common Venue  \
35     English Restaurant           Food Service    Empanada Restaurant   

   23th Most Common Venue       24th Most Common Venue 25th Most Common Venue  \
35      Electronics Store  Eastern European Restaurant            Dry Cleaner   

   26th Most Common Venue 27th Most Common Venue 28th Most Common Venue  \
35                Dog Run                  Diner     Dim Sum Restaurant   

   29th Most Common Venue 30th Most Common Venue 31th Most Common Venue  \
35           Dessert Shop       Department Store          Deli / Bodega   

   32th Most Common Venue 33th Most Common Venue 34th Most Common Venue  \
35           Dance Studio             Food Court      French Restaurant   

   35th Most Common Venue 36th Most Common Venue 37th Most Common Venue  \
35             Food Truck               Fountain                  Hotel   

   38th Most Common Venue 39th Most Common Venue 40th Most Common Venue  \
35          Hot Dog Joint                 Hostel             Hobby Shop   

   41th Most Common Venue 42th Most Common Venue 43th Most Common Venue  \
35         History Museum          Historic Site         Hardware Store   

   44th Most Common Venue 45th Most Common Venue 46th Most Common Venue  \
35        Harbor / Marina         Gymnastics Gym   Gym / Fitness Center   

   47th Most Common Venue 48th Most Common Venue 49th Most Common Venue  \
35                    Gym          Grocery Store           Gourmet Shop   

   50th Most Common Venue  
35          Go Kart Track

#### Cluster 9

In [66]:
buenosaires_merged.loc[buenosaires_merged['Cluster Labels'] == 8,buenosaires_merged.columns[[0] + list(range(5, buenosaires_merged.shape[1]))]]

neighborhood      radius  Cluster Labels 1st Most Common Venue  \
7   MONTE CASTRO  685.892645               8              Bus Stop   
11  CONSTITUCION  613.482482               8              Bus Stop   

   2nd Most Common Venue   3rd Most Common Venue 4th Most Common Venue  \
7            Pizza Place                    Café        Ice Cream Shop   
11                  Café  Argentinian Restaurant          Soccer Field   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
7              BBQ Joint           Coffee Shop                Bakery   
11                 Hotel             BBQ Joint           Pizza Place   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
7   Argentinian Restaurant                 Plaza                Dog Run   
11             Coffee Shop           Candy Store         Shopping Plaza   

   11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
7          Farmers Market             Food Court      Food & Drink Shop   
11            Bus Station                   Pool          Metro Station   

   14th Most Common Venue 15th Most Common Venue 16th Most Common Venue  \
7                    Food           Dessert Shop            Flower Shop   
11      German Restaurant                  Plaza    Indie Movie Theater   

   17th Most Common Venue 18th Most Common Venue 19th Most Common Venue  \
7             Flea Market     Dim Sum Restaurant            Fish Market   
11          Grocery Store            Flea Market             Hobby Shop   

   20th Most Common Venue 21th Most Common Venue 22th Most Common Venue  \
7    Fast Food Restaurant                Exhibit     Falafel Restaurant   
11            Fish Market                 Hostel   Fast Food Restaurant   

   23th Most Common Venue 24th Most Common Venue 25th Most Common Venue  \
7                   Diner            Event Space          Event Service   
11         Farmers Market     Falafel Restaurant                Exhibit   

   26th Most Common Venue 27th Most Common Venue 28th Most Common Venue  \
7              Food Truck     English Restaurant    Empanada Restaurant   
11            Event Space          Event Service     English Restaurant   

   29th Most Common Venue       30th Most Common Venue  \
7       Electronics Store  Eastern European Restaurant   
11    Empanada Restaurant            Electronics Store   

         31th Most Common Venue 32th Most Common Venue 33th Most Common Venue  \
7                   Dry Cleaner           Food Service      French Restaurant   
11  Eastern European Restaurant            Dry Cleaner                Dog Run   

   34th Most Common Venue 35th Most Common Venue 36th Most Common Venue  \
7                Fountain          Deli / Bodega              Hotel Bar   
11                  Diner     Dim Sum Restaurant          Hot Dog Joint   

   37th Most Common Venue 38th Most Common Venue 39th Most Common Venue  \
7                   Hotel          Hot Dog Joint                 Hostel   
11           Dessert Shop       Department Store         History Museum   

   40th Most Common Venue 41th Most Common Venue 42th Most Common Venue  \
7              Hobby Shop         History Museum          Historic Site   
11            Flower Shop           Gourmet Shop          Historic Site   

   43th Most Common Venue 44th Most Common Venue 45th Most Common Venue  \
7          Hardware Store        Harbor / Marina         Gymnastics Gym   
11          Go Kart Track              Gift Shop                    Gym   

   46th Most Common Venue 47th Most Common Venue 48th Most Common Venue  \
7    Gym / Fitness Center                    Gym          Grocery Store   
11  General Entertainment                Gay Bar              Gastropub   

   49th Most Common Venue 50th Most Common Venue  
7            Gourmet Shop          Go Kart Track  
11            Gas Station          Garden Center

#### Cluster 10

In [67]:
buenosaires_merged.loc[buenosaires_merged['Cluster Labels'] == 9,buenosaires_merged.columns[[0] + list(range(5, buenosaires_merged.shape[1]))]]

neighborhood      radius  Cluster Labels 1st Most Common Venue  \
26  PARQUE CHAS  498.053187               9                 Plaza   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
26         Grocery Store             BBQ Joint   Leather Goods Store   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
26  Gym / Fitness Center                  Café           Pizza Place   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
26           Fish Market  Fast Food Restaurant          Event Service   

   11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
26            Flea Market         Farmers Market            Flower Shop   

   14th Most Common Venue 15th Most Common Venue 16th Most Common Venue  \
26                   Food      Food & Drink Shop     Falafel Restaurant   

   17th Most Common Venue 18th Most Common Venue 19th Most Common Venue  \
26                Exhibit            Event Space          Women's Store   

   20th Most Common Venue 21th Most Common Venue 22th Most Common Venue  \
26     English Restaurant    Empanada Restaurant           Food Service   

   23th Most Common Venue       24th Most Common Venue 25th Most Common Venue  \
26      Electronics Store  Eastern European Restaurant            Dry Cleaner   

   26th Most Common Venue 27th Most Common Venue 28th Most Common Venue  \
26                Dog Run                  Diner     Dim Sum Restaurant   

   29th Most Common Venue 30th Most Common Venue 31th Most Common Venue  \
26           Dessert Shop       Department Store          Deli / Bodega   

   32th Most Common Venue 33th Most Common Venue 34th Most Common Venue  \
26             Food Court               Fountain             Food Truck   

   35th Most Common Venue 36th Most Common Venue 37th Most Common Venue  \
26           Gourmet Shop              Hotel Bar                  Hotel   

   38th Most Common Venue 39th Most Common Venue 40th Most Common Venue  \
26          Hot Dog Joint                 Hostel             Hobby Shop   

   41th Most Common Venue 42th Most Common Venue 43th Most Common Venue  \
26         History Museum          Historic Site         Hardware Store   

   44th Most Common Venue 45th Most Common Venue 46th Most Common Venue  \
26        Harbor / Marina         Gymnastics Gym                    Gym   

   47th Most Common Venue 48th Most Common Venue 49th Most Common Venue  \
26          Go Kart Track           Cupcake Shop              Gift Shop   

   50th Most Common Venue  
26      German Restaurant

# DISCUSSION

# Notes and Observations

## Goal of the work

As stated initially, the goal is to find the most interesting cluster of neighborhoods to install a Pizza Restaurant ("Pizza Place", in terminology of the Foursquare API). 

We are considering for this work that the interest is to install a high-end touristic oriented Pizza Shop, and not a simple family business, so the idea is to compete in an interesting neighborhood, that shares characteristics with neighborhoods with successful "Pizza Places", but still is the less populated with business of this type from its group ("cluster").

## A Few Important Model Limitations

It is to note that, among neighborhoods, many different economic and development indicators could be found. For this regards, venue types were expected in some way to be representative of economic development, however a further analysis could consider more specific and precise indicators, as this study only focuses on “venue types” within neighborhood locations.

Venue types, on the other hand, are only obtained by the Foursquare API. This leaves outside consideration a lot of businesses and venues that are not registered in this geographical information service. Crossing different geographical services could help to enhance the results of this study. Also, venue types are considered as presented by this API. Grouping all types of restaurants, for example, could also improve neighborhood characterization.

## Single Neighborhood Clusters

Neighborhood classification for this work is achieved by most common venue types. The amount of "most common venue types" and the total of "clusters" for neighborhood classification were the 2 main variables to play with.

The occurrence of single neighborhood clusters appeared to be a big deal when running the K-means cluster algorithm with 5 clusters and only the 10 most common venues, leaving 4 clusters with only one neighborhood and one with all the rest. Increasing the numbers to 10 clusters and 50 most common venue types, still 5 clusters only contain more than one neighborhood, so that is to say that differences of single neighborhood clusters, with this classification criteria, are quite stable.

Single neighborhood clusters, classified by this method, were found to contain in general not the most developed neighborhoods of the city in general. These neighborhoods will be discarded, because it is of interest to install a competitive business, and not to find a hot-spot in areas that are not common in terms of commercial venues, given their apparent unique characteristics in relation to the most traditional neighborhoods of the city.

## Most Interesting Clusters

After the previously mentioned considerations, clusters 1, 2, 3, 4, and 9 remained for further analysis to be selected as most interesting to determine the best candidates.

### Cluster 1
This cluster would be the undisputable winner, according to the criteria previously established. All four neighborhoods of this cluster have “Pizza Place” as the most common venue type, however this leaves no room to select the “best candidate” of this cluster to recommend. Given this finding, this cluster is finally not recommended for a new pizza restaurant, given it seems to be saturated for this type of business. 
As a side comment, these 4 neighborhoods are not the most developed of the city. This opens the suggestion that a new further research with some more specific socio economic indicators could be of some use for this research.

### Cluster 2
Boedo and Vélez Sarsfield were found to share the same cluster alone. Boedo has “Pizza Place” as the 4th more common venue, and Vélez Sarsfield has it as its 11th. Among the two, Vélez Sarsfield would be the most recommendable neighborhood for a new Pizza Restaurant.

### Cluster 3
This is “the” cluster, containing 31 out of the total 48 neighborhoods. This big cluster could suggest that further refinement classification methods could be of good use, to refine the results of this work. On this cluster, 21 out of 31 neighborhoods have “Pizza Place” on their top ten most common venues, so this could be considered a cluster that groups neighborhoods with common characteristics that make pizza restaurants prosper.
Good candidates of this cluster could be considered the neighborhoods that don’t have “Pizza Places” among their top ten most common venues. Those neighborhoods would be:

#### CLUSTER 3 RECOMMENDED NEIGHBORHOODS
| NEIGHBORHOOD |“PIZZA PLACES” commonness position |
| --- | --- |
| Palermo | >50th |
| Puerto Madero | >50th |
| Floresta | >50th |
| Retiro | >50th |
| Versalles | >50th |
| Saavedra | 44th |
| Monserrat | 20th |
| Recoleta | 18th |
| Villa Ortúzar | 16th |
| Villa Santa Rita | 12th |

### Cluster 4
This cluster has only 2 neighborhoods with “Pizza Places” in their top ten venue types (3rd for San Cristóbal and 10th for Villa General Mitre) and 2 neighborhoods without “Pizza Places” in their top 50 venue types, so the cluster could not be determined to be significant to group convenient neighborhoods for Pizza Restaurants.

### Cluster 9
This cluster only contains two neighborhoods, for which “Pizza Places” is 2nd and 7th respectively. The cluster, similar to cluster 1, seems to group adequate neighborhoods for Pizza Restaurants, however all the members seem to be highly saturated with this type of venue. No recommendation can be extended from this cluster, then, however the neighborhood of Constitución could be established as more convenient than Monte Castro.


# CONCLUSSIONS

* Cluster 2 is the winner in terms of the most successful cluster for Pizza Places within the city, followed by the biggest, cluster number 6, and cluster 1 should maybe be discarded.

* Boedo seems to host a lot of "Pizza Places", however it has similarities with neighborhoods that don't seem to be prosperous for this type of venues. May Boedo be a valid singularity or an overpopulated neighborhood for "Pizza Places", if the most common venue type is representative for neighborhood characteristics.

* Mataderos neighborhood, from cluster 2, according to the venue types criteria, has a lot of common with neighborhoods that host successfully many "Pizza Places", but seems not to have a lot of these type of venues. May it be an opportunity for a new business open or a singular case obtained with this methodology that should be discarded.

* Monserrat is another interesting neighborhood from cluster 2, as it has "Pizza Places" still among the 50 "most common venue types", however in the 22nd position, so it may not look as a very crowded neighborhood for a "Pizza Place", but still an interesting neighborhood from the winner cluster. The Monserrat neighborhood, is a very touristic neighborhood between the Presidential House (Casa Rosada) and the Congress of Argentina, near the "Obelisk", the most iconic monument of the city.

* From cluster 6, with the criteria of this analysis, winner neighborhoods should be the less populated with "Pizza Places", if the 2nd cluster place is still OK for the analysis. These neighborhoods are, as they were previously mentioned: "Villa Real", "Villa Lugano", "Agronomía", "Villa Ortúzar", "Palermo", "Villa Pueyrredón", "Versalles", "Puerto Madero" and "Recoleta". Palermo, Puerto Madero and Recoleta are among the most wealthy neighborhoods of the city and have an important of touristic flow. Versalles, Villa Real, Villa Lugano and Villa Pueyrredón are border neighborhoods of the city, near the suburban area. Agronomía and Villar Ortúzar are still within the central part of the city, however they might not be as developed and touristic as the first mentioned group of Palermo, Puerto Madero and Recoleta. All these mentioned neighborhoods could be considered candiates to open a new "Pizza Place" or for further discard, if they are considered to be a singularity occurred within this data analysis.

* Limitations of this analysis are plenty: neighborhood classification according to most common venue types might be insufficient to really determine the deep nature of neighborhoods. Average income, touristic flow and cultural interest, for example, are excluded from this analysis and are expected in some way to be reflected by the most common type of venues each neighborhood hosts, however a deeper consideration of these matters could enlighten this analysis greatly.

### Thank you for reviewing this lab!

This lab is a final task for the Coursera specialization "Data Science", organized by IBM.

Author: [Santiago Maraggi](http://www.linkedin.com/in/santiagomaraggi/)

This notebook is inspired in the one of reference provided by [Alex Aklson](https://www.linkedin.com/in/aklson/) and [Polong Lin](https://www.linkedin.com/in/polonglin/). 

This notebook is part of a course on **Coursera** called *Applied Data Science Capstone*. If you accessed this notebook outside the course, you can take this course online by clicking [here](http://cocl.us/DP0701EN_Coursera_Week3_LAB2).

<hr>

Copyright &copy; 2018 [Cognitive Class](https://cognitiveclass.ai/?utm_source=bducopyrightlink&utm_medium=dswb&utm_campaign=bdu). This notebook and its source code are released under the terms of the [MIT License](https://bigdatauniversity.com/mit-license/).